In [13]:
import pandas as pd
import matplotlib.pyplot as plt
from sklearn import metrics
import xgboost
from sklearn.model_selection import cross_val_predict
import shap
from sklearn.model_selection import train_test_split
import numpy as np
%matplotlib inline

In [15]:
df = pd.read_csv("police-shootings/database.csv")

In [4]:
len(df)

2142

In [5]:
df.columns

Index(['id', 'name', 'date', 'manner_of_death', 'armed', 'age', 'gender',
       'race', 'city', 'state', 'signs_of_mental_illness', 'threat_level',
       'flee', 'body_camera'],
      dtype='object')

In [6]:
df.head()

id                name        date   manner_of_death       armed   age  \
0   3          Tim Elliot  2015-01-02              shot         gun  53.0   
1   4    Lewis Lee Lembke  2015-01-02              shot         gun  47.0   
2   5  John Paul Quintero  2015-01-03  shot and Tasered     unarmed  23.0   
3   8     Matthew Hoffman  2015-01-04              shot  toy weapon  32.0   
4   9   Michael Rodriguez  2015-01-04              shot    nail gun  39.0   

  gender race           city state  signs_of_mental_illness threat_level  \
0      M    A        Shelton    WA                     True       attack   
1      M    W          Aloha    OR                    False       attack   
2      M    H        Wichita    KS                    False        other   
3      M    W  San Francisco    CA                     True       attack   
4      M    H          Evans    CO                    False       attack   

          flee  body_camera  
0  Not fleeing        False  
1  Not fleeing        False  
2  Not fleeing        False  
3  Not fleeing        False  
4  Not fleeing        False

In [16]:
# Feature Engineering + transformation
df = df[df["gender"].notnull()]
df = df[df["race"].notnull()]
df = df[df["armed"].notnull()]
df.drop("flee", axis=1, inplace=True)
df.drop("body_camera", axis=1, inplace=True)
race_map = {
     'A': 0,
     'W': 1, 
     'H': 0, 
     'B': 0, 
     'O': 0, 
     'N': 0   
}
df["race"] = df["race"].map(race_map)
df = pd.concat([df, pd.get_dummies(df["state"])], axis=1)
df = pd.concat([df, pd.get_dummies(df["manner_of_death"])], axis=1)
df = pd.concat([df, pd.get_dummies(df["threat_level"])], axis=1)
df = pd.concat([df, pd.get_dummies(df["armed"])], axis=1)
df.drop("state", axis=1, inplace=True)
df.drop("manner_of_death", axis=1, inplace=True)
df.drop("threat_level", axis=1, inplace=True)
df.drop("armed", axis=1, inplace=True)
mental_illness_map = {
    True: 1,
    False: 0
}
gender_map = {
    "M": 0,
    "F": 1
}
df["signs_of_mental_illness"] = df["signs_of_mental_illness"].map(mental_illness_map)
df["gender"] = df["gender"].map(gender_map)
df["month"] = [elem.month for elem in pd.to_datetime(df["date"])]
df["day"] = [elem.day for elem in pd.to_datetime(df["date"])]
df["year"] = [elem.year for elem in pd.to_datetime(df["date"])]
df.drop("date", axis=1, inplace=True)

In [56]:
df.head()

id                name   age  gender race           city  \
0   3          Tim Elliot  53.0       0    A        Shelton   
1   4    Lewis Lee Lembke  47.0       0    W          Aloha   
2   5  John Paul Quintero  23.0       0    H        Wichita   
3   8     Matthew Hoffman  32.0       0    W  San Francisco   
4   9   Michael Rodriguez  39.0       0    H          Evans   

   signs_of_mental_illness  AK  AL  AR  ...   straight edge razor  sword  \
0                        1   0   0   0  ...                     0      0   
1                        0   0   0   0  ...                     0      0   
2                        0   0   0   0  ...                     0      0   
3                        1   0   0   0  ...                     0      0   
4                        0   0   0   0  ...                     0      0   

   toy weapon  unarmed  undetermined  unknown weapon  vehicle  month  day  \
0           0        0             0               0        0      1    2   
1           0        0             0               0        0      1    2   
2           0        1             0               0        0      1    3   
3           1        0             0               0        0      1    4   
4           0        0             0               0        0      1    4   

   year  
0  2015  
1  2015  
2  2015  
3  2015  
4  2015  

[5 rows x 129 columns]

In [17]:
df.drop("id", inplace=True, axis=1)
df.drop("name", inplace=True, axis=1)
df.drop("city", inplace=True, axis=1)

In [66]:
df["race"].unique()

array(['A', 'W', 'H', 'B', 'O', 'N'], dtype=object)

In [18]:
df = df[df["age"].notnull()]
y = df["race"]
X = df.drop("race", axis=1)

In [22]:
X = X[list(set(X.columns.tolist()))]

In [23]:
xgb_full = xgboost.DMatrix(X, label=y)

# create a train/test split
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=7)
xgb_train = xgboost.DMatrix(X_train, label=y_train)
xgb_test = xgboost.DMatrix(X_test, label=y_test)
# use validation set to choose # of trees
params = {
    "eta": 0.002,
    "max_depth": 3,
    "objective": "survival:cox",
    "subsample": 0.5
}
model_train = xgboost.train(params, xgb_train, 10000, evals = [(xgb_test, "test")], verbose_eval=1000)
# train final model on the full data set
params = {
    "eta": 0.002,
    "max_depth": 3, 
    "objective": "survival:cox",
    "subsample": 0.5
}
model = xgboost.train(params, xgb_full, 5000, evals = [(xgb_full, "test")], verbose_eval=1000)

ValueError: feature_names must be unique

In [7]:
from IPython.display import Image  
from sklearn.tree import export_graphviz
import graphviz
import pydotplus
from io import StringIO  

cart_clf.fit(X, y)
dot_data = StringIO()
export_graphviz(cart_clf, out_file=dot_data, feature_names=X.columns.tolist(), 
                filled=True, rounded=True, special_characters=True)
graph = pydotplus.graph_from_dot_data(dot_data.getvalue())  
Image(graph.create_png())

In [27]:
features = sorted(list(zip(X.columns.tolist(), cart_clf.feature_importances_)), 
       key=lambda t:t[1], reverse=True)
for feature in features[:10]:
    print(feature)

('age', 0.22493395038266403)
('day', 0.1626058783659278)
('month', 0.11928124113218921)
('year', 0.04770578677516514)
('CA', 0.025197748436013658)
('signs_of_mental_illness', 0.022435734685181816)
('knife', 0.0215943595872303)
('FL', 0.0193818512180609)
('gun', 0.019003444563964095)
('other', 0.015730545612754568)
